# Image Classification with AWS SageMaker and Keras with backend MXNet
<hr>
## Handle the dataset
1. Download the dataset
2. Uncompress it
3. Preprocess the data
4. Save the data x_train, y_train, x_test and y_test to pickle file

Folder Structure:

data/train: save x_train and y_train as pickled files with names train-x and train-y repsectively<br>
data/validation: save x_test and y_test as pickled files with names test-x and test-y repsectively

## Download Dataset

In [ ]:
!wget https://www.cs.utoronto.ca/~kriz/cifar-10-python.tar.gz
!tar xzvf cifar-10-python.tar.gz
!rm -rf cifar-10-python.tar.gz

In [ ]:
import pickle
import numpy as np
from os import listdir
from os.path import isfile, join
import os

# Function to unpickle the dataset
def unpickle_all_data(directory):
    
    # Initialize the variables
    train = dict()
    test = dict()
    train_x = []
    train_y = []
    test_x = []
    test_y = []
    
    # Iterate through all files that we want, train and test
    # Train is separated into batches
    for filename in listdir(directory):
        if isfile(join(directory, filename)):
            
            # The train data
            if 'data_batch' in filename:
                print('Handing file: %s' % filename)
                
                # Opent the file
                with open(directory + '/' + filename, 'rb') as fo:
                    data = pickle.load(fo, encoding='bytes')

                if 'data' not in train:
                    train['data'] = data[b'data']
                    train['labels'] = np.array(data[b'labels'])
                else:
                    train['data'] = np.concatenate((train['data'], data[b'data']))
                    train['labels'] = np.concatenate((train['labels'], data[b'labels']))
            # The test data
            elif 'test_batch' in filename:
                print('Handing file: %s' % filename)
                
                # Open the file
                with open(directory + '/' + filename, 'rb') as fo:
                    data = pickle.load(fo, encoding='bytes')
                
                test['data'] = data[b'data']
                test['labels'] = data[b'labels']
    
    # Manipulate the data to the propper format
    for image in train['data']:
        train_x.append(np.transpose(np.reshape(image,(3, 32,32)), (1,2,0)))
    train_y = [label for label in train['labels']]
    
    for image in test['data']:
        test_x.append(np.transpose(np.reshape(image,(3, 32,32)), (1,2,0)))
    test_y = [label for label in test['labels']]
    
    # Transform the data to np array format
    train_x = np.array(train_x)
    train_y = np.array(train_y)
    test_x = np.array(test_x)
    test_y = np.array(test_y)
    
    return (train_x, train_y), (test_x, test_y)

(x_train, y_train), (x_test, y_test) = unpickle_all_data(os.getcwd() + '/cifar-10-batches-py/')

with open('data/validation/test-x', 'wb') as handle:
    pickle.dump(x_test, handle, protocol=pickle.HIGHEST_PROTOCOL)
with open('data/validation/test-y', 'wb') as handle:
    pickle.dump(y_test, handle, protocol=pickle.HIGHEST_PROTOCOL)
with open('data/train/train-x', 'wb') as handle:
    pickle.dump(x_train, handle, protocol=pickle.HIGHEST_PROTOCOL)
with open('data/train/train-y', 'wb') as handle:
    pickle.dump(y_train, handle, protocol=pickle.HIGHEST_PROTOCOL)

## Start a SageMaker session

In [1]:
import sagemaker
sess = sagemaker.Session()
role = sagemaker.get_execution_role()
account = sess.boto_session.client('sts').get_caller_identity()['Account']
region = sess.boto_session.region_name

## Validate your configuration

1. DockerFile for your custom container that holds your code
2. keras.json configuration
3. python file that defined your model

In [2]:
!cat Dockerfile.gpu

FROM nvidia/cuda:9.0-runtime

RUN apt-get update && \
    apt-get -y install build-essential libopencv-dev libopenblas-dev libjemalloc-dev libgfortran3 \
    python-dev python3-dev python3-pip wget curl

COPY cifar_10_keras.py /opt/program/train
RUN chmod +x /opt/program/train

RUN mkdir /root/.keras
COPY keras.json /root/.keras/

RUN pip3 install mxnet-cu90 --upgrade --pre && \
    pip3 install keras-mxnet --upgrade --pre

RUN rm -rf /var/lib/apt/lists/*
RUN rm -rf /root/.cache

ENV PYTHONDONTWRITEBYTECODE=1 \
    PYTHONUNBUFFERED=1 \
    LD_LIBRARY_PATH="${LD_LIBRARY_PATH}:/usr/local/lib"

ENV PATH="/opt/program:${PATH}"

WORKDIR /opt/program

In [ ]:
!cat keras.jsonas.json

In [ ]:
!tail cifar_10_keras.py

## Copy the Dockerfile, keras.json and cifar_10_keras.py into build folder

In [3]:
# Copy Dockerfiles
!cp Dockerfile.* build/

In [4]:
# Copy training script and config file
!cp cifar_10_keras.py build/
!cp keras.json build/

## GPU Settings for training your algorithm

In [2]:
repo_name = 'keras-mxnet-gpu' # ECR repository
image_tag = 'keras-mxnet1.2.0-gpu-py3' # ECR image tag
base_job_name = 'keras-mxnet-cifar-10-cnn' # SageMaker training prefix

%env dockerfile Dockerfile.gpu

train_instance_type='ml.p3.2xlarge'
gpu_count=1
batch_size=64

env: dockerfile=Dockerfile.gpu


## Common settings

In [3]:
%env account {account}
%env region {region}
%env repo_name {repo_name}
%env image_tag {image_tag}

env: account=988095220859
env: region=us-west-2
env: repo_name=keras-mxnet-gpu
env: image_tag=keras-mxnet1.2.0-gpu-py3


## Create Repository and login

Before advancing to this step make sure you have an ECR up and running with the same name as in the vaiable `repo_name`

If you encounter an authentication error, make sure you have given the appropriate access to the repository

In [8]:
%%sh

aws ecr describe-repositories --repository-names $repo_name > /dev/null 2>&1
if [ $? -ne 0 ]
then
    aws ecr create-repository --repository-name $repo_name > /dev/null
fi

$(aws ecr get-login --region $region --no-include-email)

Login Succeeded


WARNING! Using --password via the CLI is insecure. Use --password-stdin.


## Build the Docker image

In [115]:
%cd build
!docker build -t $image_tag -f $dockerfile .
%cd ..

/home/ec2-user/SageMaker/build
Sending build context to Docker daemon  10.75kB
Step 1/12 : FROM nvidia/cuda:9.0-runtime
 ---> 5d26a867c5bf
Step 2/12 : RUN apt-get update &&     apt-get -y install build-essential libopencv-dev libopenblas-dev libjemalloc-dev libgfortran3     python-dev python3-dev python3-pip wget curl
 ---> Running in 6665ab5acc33
Get:1 http://security.ubuntu.com/ubuntu xenial-security InRelease [107 kB]
Get:2 http://archive.ubuntu.com/ubuntu xenial InRelease [247 kB]
Ign:3 https://developer.download.nvidia.com/compute/cuda/repos/ubuntu1604/x86_64  InRelease
Ign:4 https://developer.download.nvidia.com/compute/machine-learning/repos/ubuntu1604/x86_64  InRelease
Get:5 https://developer.download.nvidia.com/compute/cuda/repos/ubuntu1604/x86_64  Release [564 B]
Get:6 https://developer.download.nvidia.com/compute/machine-learning/repos/ubuntu1604/x86_64  Release [564 B]
Get:7 https://developer.download.nvidia.com/compute/cuda/repos/ubuntu1604/x86_64  Release.gpg [801 B]
Get:

1 upgraded, 395 newly installed, 0 to remove and 3 not upgraded.
Need to get 235 MB of archives.
After this operation, 979 MB of additional disk space will be used.
Get:1 http://archive.ubuntu.com/ubuntu xenial-updates/main amd64 perl-base amd64 5.22.1-9ubuntu0.5 [1284 kB]
Get:2 http://archive.ubuntu.com/ubuntu xenial/main amd64 libatm1 amd64 1:2.5.1-1.5 [24.2 kB]
Get:3 http://archive.ubuntu.com/ubuntu xenial/main amd64 libmnl0 amd64 1.0.3-5 [12.0 kB]
Get:4 http://archive.ubuntu.com/ubuntu xenial-updates/main amd64 libpython3.5-minimal amd64 3.5.2-2ubuntu0~16.04.4 [523 kB]
Get:5 http://archive.ubuntu.com/ubuntu xenial-updates/main amd64 libexpat1 amd64 2.1.0-7ubuntu0.16.04.3 [71.2 kB]
Get:6 http://archive.ubuntu.com/ubuntu xenial-updates/main amd64 python3.5-minimal amd64 3.5.2-2ubuntu0~16.04.4 [1597 kB]
Get:7 http://archive.ubuntu.com/ubuntu xenial/main amd64 python3-minimal amd64 3.5.1-3 [23.3 kB]
Get:8 http://archive.ubuntu.com/ubuntu xenial/main amd64 mime-support all 3.59ubuntu1 [

Get:81 http://archive.ubuntu.com/ubuntu xenial-updates/main amd64 iproute2 amd64 4.3.0-1ubuntu3.16.04.3 [522 kB]
Get:82 http://archive.ubuntu.com/ubuntu xenial-updates/main amd64 ifupdown amd64 0.8.10ubuntu1.4 [54.9 kB]
Get:83 http://archive.ubuntu.com/ubuntu xenial-updates/main amd64 libisc-export160 amd64 1:9.10.3.dfsg.P4-8ubuntu1.10 [153 kB]
Get:84 http://archive.ubuntu.com/ubuntu xenial-updates/main amd64 libdns-export162 amd64 1:9.10.3.dfsg.P4-8ubuntu1.10 [666 kB]
Get:85 http://archive.ubuntu.com/ubuntu xenial-updates/main amd64 isc-dhcp-client amd64 4.3.3-5ubuntu12.10 [224 kB]
Get:86 http://archive.ubuntu.com/ubuntu xenial-updates/main amd64 isc-dhcp-common amd64 4.3.3-5ubuntu12.10 [105 kB]
Get:87 http://archive.ubuntu.com/ubuntu xenial/main amd64 libbsd0 amd64 0.8.2-1 [41.7 kB]
Get:88 http://archive.ubuntu.com/ubuntu xenial/main amd64 libxtables11 amd64 1.6.0-2ubuntu3 [27.2 kB]
Get:89 http://archive.ubuntu.com/ubuntu xenial/main amd64 netbase all 5.3 [12.9 kB]
Get:90 http://arch

Get:158 http://archive.ubuntu.com/ubuntu xenial/main amd64 libatk1.0-data all 2.18.0-1 [17.1 kB]
Get:159 http://archive.ubuntu.com/ubuntu xenial/main amd64 libatk1.0-0 amd64 2.18.0-1 [56.9 kB]
Get:160 http://archive.ubuntu.com/ubuntu xenial/main amd64 gir1.2-atk-1.0 amd64 2.18.0-1 [17.6 kB]
Get:161 http://archive.ubuntu.com/ubuntu xenial/main amd64 gir1.2-freedesktop amd64 1.46.0-3ubuntu1 [5742 B]
Get:162 http://archive.ubuntu.com/ubuntu xenial/main amd64 libjpeg8 amd64 8c-2ubuntu8 [2194 B]
Get:163 http://archive.ubuntu.com/ubuntu xenial-updates/main amd64 libtiff5 amd64 4.0.6-1ubuntu0.4 [148 kB]
Get:164 http://archive.ubuntu.com/ubuntu xenial-updates/main amd64 libgdk-pixbuf2.0-common all 2.32.2-1ubuntu1.4 [10.5 kB]
Get:165 http://archive.ubuntu.com/ubuntu xenial-updates/main amd64 libgdk-pixbuf2.0-0 amd64 2.32.2-1ubuntu1.4 [158 kB]
Get:166 http://archive.ubuntu.com/ubuntu xenial-updates/main amd64 gir1.2-gdkpixbuf-2.0 amd64 2.32.2-1ubuntu1.4 [8090 B]
Get:167 http://archive.ubuntu.com

Get:234 http://archive.ubuntu.com/ubuntu xenial/main amd64 libblas-common amd64 3.6.0-2ubuntu2 [5342 B]
Get:235 http://archive.ubuntu.com/ubuntu xenial/main amd64 libblas3 amd64 3.6.0-2ubuntu2 [147 kB]
Get:236 http://archive.ubuntu.com/ubuntu xenial/main amd64 libblas-dev amd64 3.6.0-2ubuntu2 [153 kB]
Get:237 http://archive.ubuntu.com/ubuntu xenial/main amd64 libcairo-gobject2 amd64 1.14.6-1 [17.3 kB]
Get:238 http://archive.ubuntu.com/ubuntu xenial/main amd64 libcairo-script-interpreter2 amd64 1.14.6-1 [54.3 kB]
Get:239 http://archive.ubuntu.com/ubuntu xenial-updates/main amd64 libexpat1-dev amd64 2.1.0-7ubuntu0.16.04.3 [115 kB]
Get:240 http://archive.ubuntu.com/ubuntu xenial/main amd64 libpng12-dev amd64 1.2.54-1ubuntu1 [184 kB]
Get:241 http://archive.ubuntu.com/ubuntu xenial-updates/main amd64 libfreetype6-dev amd64 2.6.1-0.1ubuntu2.3 [956 kB]
Get:242 http://archive.ubuntu.com/ubuntu xenial-updates/main amd64 libfontconfig1-dev amd64 2.11.94-0ubuntu1.1 [658 kB]
Get:243 http://archive

...

Selecting previously unselected package libopencv-videostab2.4v5:amd64.
Preparing to unpack .../libopencv-videostab2.4v5_2.4.9.1+dfsg-1.5ubuntu1_amd64.deb ...
Unpacking libopencv-videostab2.4v5:amd64 (2.4.9.1+dfsg-1.5ubuntu1) ...
Selecting previously unselected package libopencv-videostab-dev:amd64.
Preparing to unpack .../libopencv-videostab-dev_2.4.9.1+dfsg-1.5ubuntu1_amd64.deb ...
Unpacking libopencv-videostab-dev:amd64 (2.4.9.1+dfsg-1.5ubuntu1) ...
Selecting previously unselected package libopencv-stitching2.4v5:amd64.
Preparing to unpack .../libopencv-stitching2.4v5_2.4.9.1+dfsg-1.5ubuntu1_amd64.deb ...
Unpacking libopencv-stitching2.4v5:amd64 (2.4.9.1+dfsg-1.5ubuntu1) ...
Selecting previously unselected package libopencv-stitching-dev:amd64.
Preparing to unpack .../libopencv-stitching-dev_2.4.9.1+dfsg-1.5ubuntu1_amd64.deb ...
Unpacking libopencv-stitching-dev:amd64 (2.4.9.1+dfsg-1.5ubuntu1) ...
Selecting previously unselected package libopencv-ocl2.4v5:amd64.
Preparing to unpack 

Setting up fonts-dejavu-core (2.35-1) ...
Setting up ucf (3.0036) ...
debconf: unable to initialize frontend: Dialog
debconf: (TERM is not set, so the dialog frontend is not usable.)
debconf: falling back to frontend: Readline
Setting up fontconfig-config (2.11.94-0ubuntu1.1) ...
Setting up libpng12-0:amd64 (1.2.54-1ubuntu1) ...
Setting up libfreetype6:amd64 (2.6.1-0.1ubuntu2.3) ...
Setting up libfontconfig1:amd64 (2.11.94-0ubuntu1.1) ...
Setting up fontconfig (2.11.94-0ubuntu1.1) ...
Regenerating fonts cache... done.
Setting up libcrystalhd3:amd64 (1:0.0~git20110715.fdd2f19-11build1) ...
Setting up libgsm1:amd64 (1.0.13-4) ...
Setting up x11-common (1:7.7+13ubuntu3) ...
debconf: unable to initialize frontend: Dialog
debconf: (TERM is not set, so the dialog frontend is not usable.)
debconf: falling back to frontend: Readline
update-rc.d: warning: start and stop actions are no longer supported; falling back to defaults
invoke-rc.d: could not determine current runlevel
invoke-rc.d: polic

Setting up libpangoxft-1.0-0:amd64 (1.38.1-1) ...
Setting up gir1.2-pango-1.0:amd64 (1.38.1-1) ...
Setting up libavahi-common-data:amd64 (0.6.32~rc+dfsg-1ubuntu2.2) ...
Setting up libavahi-common3:amd64 (0.6.32~rc+dfsg-1ubuntu2.2) ...
Setting up libavahi-client3:amd64 (0.6.32~rc+dfsg-1ubuntu2.2) ...
Setting up libcups2:amd64 (2.1.3-4ubuntu0.4) ...
Setting up libxcursor1:amd64 (1:1.1.14-1ubuntu0.16.04.1) ...
Setting up libxi6:amd64 (2:1.7.6-1) ...
Setting up libxrandr2:amd64 (2:1.5.0-1) ...
Setting up libgtk2.0-0:amd64 (2.24.30-1ubuntu1.16.04.2) ...
Setting up gir1.2-gtk-2.0 (2.24.30-1ubuntu1.16.04.2) ...
Setting up hicolor-icon-theme (0.15-0ubuntu1) ...
Setting up libaacs0:amd64 (0.8.1-1) ...
Setting up libalgorithm-diff-perl (1.19.03-1) ...
Setting up libalgorithm-diff-xs-perl (0.04-4build1) ...
Setting up libalgorithm-merge-perl (0.08-3) ...
Setting up libasprintf-dev:amd64 (0.19.7-2ubuntu3) ...
Setting up pkg-config (0.29.1-0ubuntu1) ...
Setting up libglib2.0-bin (2.48.2-0ubuntu1) .

Setting up libjpeg-dev:amd64 (8c-2ubuntu8) ...
Setting up libjbig-dev:amd64 (2.1-3.1) ...
Setting up liblzma-dev:amd64 (5.1.1alpha+20120614-2ubuntu2) ...
Setting up libtiffxx5:amd64 (4.0.6-1ubuntu0.4) ...
Setting up libtiff5-dev:amd64 (4.0.6-1ubuntu0.4) ...
Setting up libraw1394-dev:amd64 (2.1.1-2) ...
Setting up libdc1394-22-dev:amd64 (2.2.4-1) ...
Setting up libopencv-highgui-dev:amd64 (2.4.9.1+dfsg-1.5ubuntu1) ...
Setting up libopencv-objdetect2.4v5:amd64 (2.4.9.1+dfsg-1.5ubuntu1) ...
Setting up libopencv-objdetect-dev:amd64 (2.4.9.1+dfsg-1.5ubuntu1) ...
Setting up libopencv-video2.4v5:amd64 (2.4.9.1+dfsg-1.5ubuntu1) ...
Setting up libopencv-video-dev:amd64 (2.4.9.1+dfsg-1.5ubuntu1) ...
Setting up libopencv-ml2.4v5:amd64 (2.4.9.1+dfsg-1.5ubuntu1) ...
Setting up libopencv-ml-dev:amd64 (2.4.9.1+dfsg-1.5ubuntu1) ...
Setting up libopencv-legacy2.4v5:amd64 (2.4.9.1+dfsg-1.5ubuntu1) ...
Setting up libopencv-legacy-dev:amd64 (2.4.9.1+dfsg-1.5ubuntu1) ...
Setting up libcv-dev:amd64 (2.4.9.1

Requirement already up-to-date: numpy>=1.9.1 in /usr/local/lib/python3.5/dist-packages (from keras-mxnet)
  Running setup.py bdist_wheel for pyyaml: started
  Running setup.py bdist_wheel for pyyaml: finished with status 'done'
  Stored in directory: /root/.cache/pip/wheels/03/05/65/bdc14f2c6e09e82ae3e0f13d021e1b6b2481437ea2f207df3f
Successfully built pyyaml
You are using pip version 8.1.1, however version 10.0.1 is available.
You should consider upgrading via the 'pip install --upgrade pip' command.
Removing intermediate container 63ff708ffbea
 ---> 69da05479e55
Step 8/12 : RUN rm -rf /var/lib/apt/lists/*
 ---> Running in de7c7ab29c47
Removing intermediate container de7c7ab29c47
 ---> 765da6f7a5c5
Step 9/12 : RUN rm -rf /root/.cache
 ---> Running in 733ba5bcb135
Removing intermediate container 733ba5bcb135
 ---> 741b533bb030
Step 10/12 : ENV PYTHONDONTWRITEBYTECODE=1     PYTHONUNBUFFERED=1     LD_LIBRARY_PATH="${LD_LIBRARY_PATH}:/usr/local/lib"
 ---> Running in 1403906b791d
Removing i

In [116]:
# Assign a tag to the Docker image
!docker tag $image_tag $account.dkr.ecr.$region.amazonaws.com/$repo_name:latest

In [117]:
# Make sure you see your image with a tag `:latest` at the end of the name
!docker images -a

CONTAINER ID        IMAGE               COMMAND             CREATED             STATUS              PORTS               NAMES
REPOSITORY                                                     TAG                 IMAGE ID            CREATED              SIZE
988095220859.dkr.ecr.us-west-2.amazonaws.com/keras-mxnet-gpu   latest              ece2c0d4a1b1        8 seconds ago        3GB
keras-mxnet1.2.0-gpu-py3                                       latest              ece2c0d4a1b1        8 seconds ago        3GB
<none>                                                         <none>              da1283dcc7cf        8 seconds ago        3GB
<none>                                                         <none>              682220acd8ef        8 seconds ago        3GB
<none>                                                         <none>              765da6f7a5c5        9 seconds ago        3GB
<none>                                                         <none>              741b533bb030        9 

## Push docker image to ECR

In [118]:
!docker push $account.dkr.ecr.$region.amazonaws.com/$repo_name:latest

The push refers to repository [988095220859.dkr.ecr.us-west-2.amazonaws.com/keras-mxnet-gpu]

624e4cda: Preparing 
3b0bdc50: Preparing 
b3653fd2: Preparing 
f8a9efe0: Preparing 
d7cf7896: Preparing 
1c0962cd: Preparing 
ffc1b761: Preparing 
1e960549: Preparing 
72b6a6b7: Preparing 
935f5c1b: Preparing 
d18f215e: Preparing 
e103a218: Preparing 
91e51d73: Preparing 
d9e65295: Preparing 
45e78935: Preparing 
1dc646ba: Preparing 


e960549: Pushing  796.9MB/890.4MB15A

3653fd2: Pushed   1.272GB/1.269GBlatest: digest: sha256:092ee4f8f2e973faa2568f1cc18cd1692428cc76239e07d6af871d9bd7c30d3e size: 3870


## Upload dataset to S3

In [97]:
local_directory = 'data'
prefix          = repo_name+'/input'

# Upload dataset to S3 and set the train and validation path
train_input_path      = sess.upload_data(local_directory+'/train/',      key_prefix=prefix+'/train')
validation_input_path = sess.upload_data(local_directory+'/validation/', key_prefix=prefix+'/validation')

## Create an estimator and run your image

In [119]:
output_path = 's3://{}/{}/output'.format(sess.default_bucket(), repo_name)
image_name  = '{}.dkr.ecr.{}.amazonaws.com/{}:latest'.format(account, region, repo_name)

print(output_path)
print(image_name)

estimator = sagemaker.estimator.Estimator(
                       image_name=image_name,
                       base_job_name=base_job_name,
                       role=role, 
                       train_instance_count=1, 
                       train_instance_type=train_instance_type,
                       output_path=output_path,
                       sagemaker_session=sess)

estimator.set_hyperparameters(lr=0.0001, epochs=10, gpus=gpu_count, batch_size=batch_size)

s3://sagemaker-us-west-2-988095220859/keras-mxnet-gpu/output
988095220859.dkr.ecr.us-west-2.amazonaws.com/keras-mxnet-gpu:latest


## Train the algorithm

In [120]:
estimator.fit({'training': train_input_path, 'validation': validation_input_path})

INFO:sagemaker:Creating training-job with name: keras-mxnet-cifar-10-cnn-2018-06-18-14-16-16-930


..................
Using MXNet backend
Hyper parameters: {'gpus': '1', 'epochs': '100', 'lr': '0.001', 'batch_size': '64'}
Input parameters: {'training': {'TrainingInputMode': 'File', 'RecordWrapperType': 'None', 'S3DistributionType': 'FullyReplicated'}, 'validation': {'TrainingInputMode': 'File', 'RecordWrapperType': 'None', 'S3DistributionType': 'FullyReplicated'}}
Files loaded
x_train shape: (50000, 32, 32, 3)
50000 train samples
10000 test samples
/usr/local/lib/python3.5/dist-packages/keras/backend/mxnet_backend.py:89: UserWarning: MXNet Backend performs best with `channels_first` format. Using `channels_last` will significantly reduce performance due to the Transpose operations. For performance improvement, please use this API`keras.utils.to_channels_first(x_input)`to transform `channels_last` data to `channels_first` format and also please change the `image_data_format` in `keras.json` to `channels_first`.Note: `x_input` is a Numpy tensor or a list of Numpy tensorRefer to: https

536/782 [===================>..........] - ETA: 10s - loss: 1.8361 - acc: 0.3260


782/782 [==============================] - 30s 38ms/step - loss: 1.7388 - acc: 0.3631 - val_loss: 1.3465 - val_acc: 0.5066
Epoch 2/100

105/782 [===>..........................] - ETA: 16s - loss: 1.4394 - acc: 0.4836


467/782 [================>.............] - ETA: 8s - loss: 1.3965 - acc: 0.4995


...

459/782 [================>.............] - ETA: 8s - loss: 1.3670 - acc: 0.5657


782/782 [==============================] - 22s 28ms/step - loss: 1.3547 - acc: 0.5659 - val_loss: 0.9934 - val_acc: 0.6764
Epoch 100/100

 26/782 [..............................] - ETA: 13s - loss: 1.4219 - acc: 0.5319


567/782 [====================>.........] - ETA: 5s - loss: 1.3386 - acc: 0.5733


782/782 [==============================] - 22s 28ms/step - loss: 1.3501 - acc: 0.5706 - val_loss: 1.0074 - val_acc: 0.6735
Test loss: 1.007444306755066
Test accuracy: 0.6735
Saved Keras model


===== Job Complete =====
Billable seconds: 2317
